## 1. Faktorizace polynomů nad různými okruhy

In [7]:
R.<x> = ZZ[]
S.<y> = Zmod(13)[]

K.<a> = NumberField(x^2 + x + 1)
T.<z> = K[]

In [13]:
# využívám toho, že polynom x^3-1 nad Z lze přetypovat na polynom nad jakýmkoliv jiným okruhem
for F in [R, S, T]:
    print(factor(F(x^3-1)))

(x - 1) * (x^2 + x + 1)
(y + 4) * (y + 10) * (y + 12)
(z - 1) * (z - a) * (z + a + 1)


## 2. Vyčíslování hodnot polynomů

In [19]:
def tupe_vycisleni(p, a):
    res = 0
    a_power = 1
    for coeff in p:
        res += coeff * a_power
        a_power *= a
    return res

In [22]:
def horner(p, a):
    res = 0
    for coeff in reversed(list(p)):
        res = a*res + coeff
    return res

In [20]:
tupe_vycisleni(2*x^3-3*x+2, 4)

118

In [23]:
horner(2*x^3-3*x+2, 4)

118

In [35]:
for fn in ["tupe_vycisleni", "horner"]:
    print(timeit(f"{fn}(R.random_element((-1, 100), x=-2^100, y=2^100), ZZ.random_element(2^100))", number=1000))

# Sageové dosazení se dělá prostě tak, že do polynomu dosadíme jako do funkce
print(timeit("R.random_element((-1, 100), x=-2^100, y=2^100)(ZZ.random_element(2^100))", number=1000))

1000 loops, best of 3: 108 μs per loop
1000 loops, best of 3: 87.6 μs per loop
1000 loops, best of 3: 59.9 μs per loop


## 3. Násobení a dělení

In [38]:
def nasob_skolne(p, q):
    res = []
    for i, a in enumerate(p):
        for j, b in enumerate(q):
            if len(res) < i+j+1:
                res.append(a*b)
            else:
                res[i+j] += a*b
    return res

In [39]:
R(nasob_skolne(x-1, x^2+x+1))

x^3 - 1

In [41]:
# polynom p se dělí (se zbytkem) polynomem q:
def vydel(p, q):
    v = p.parent().gen()
    q_deg = q.degree()
    q_lead = q.leading_coefficient()
    res = 0
    while (p_deg := p.degree()) >= q_deg:
        coeff_ratio = p.leading_coefficient() / q_lead
        new_monom = coeff_ratio * v^(p_deg - q_deg)
        res += new_monom
        p -= new_monom * q
    return res, p

In [42]:
PQ.<w> = QQ[]

In [47]:
vydel(w^7 - w^5 + 3*w^2 + 1, 2*w^3-1)

(1/2*w^4 - 1/2*w^2 + 1/4*w, 5/2*w^2 + 1/4*w + 1)

In [48]:
divmod(w^7 - w^5 + 3*w^2 + 1, 2*w^3-1)

(1/2*w^4 - 1/2*w^2 + 1/4*w, 5/2*w^2 + 1/4*w + 1)

## 4. Karacuba pro polynomy

Myšlenka je v zásadě stejná jako pro počítání s čísly; polynomy rozdělíme na "spodní" a "horní" polovinu a násobíme rekurentně.
Pro její implementaci pro listy si ale musíme ještě dodefinovat sčítání a odčítání polynomů.

In [49]:
from itertools import zip_longest

In [68]:
# pomocná funkce, která maže nuly z konce listu
def smaz_nuly(p):
    while p and (not p[-1]):
        del p[-1]
    return p

In [66]:
# definice umožňující libovolný počet argumentů
def secti(*polys):
    return smaz_nuly([sum(ps) for ps in zip_longest(*polys, fillvalue=0)])

In [65]:
def odecti(p, q):
    return smaz_nuly([a-b for a, b in zip_longest(p, q, fillvalue=0)])

In [98]:
def karacuba(p, q):
    p, q = map(list, (p, q))
    if (len(p) < 6) or (len(q) < 6):
        return nasob_skolne(p, q)
    n = max(len(p), len(q)) // 2
    p1, p0 = p[n:], p[:n]
    q1, q0 = q[n:], q[:n]
    p1q1 = karacuba(p1, q1)
    p0q0 = karacuba(p0, q0)
    p_diff = odecti(p0, p1)
    q_diff = odecti(q1, q0) # naopak!
    pq_diff = karacuba(p_diff, q_diff)
    mixed = secti(p1q1, p0q0, pq_diff)
    return secti([0]*(2*n)+p1q1, p0q0, [0]*n+mixed)

In [82]:
R(karacuba(x^20 + x^5 + x^4 - 2*x^2 + x - 3, x^7 + 3*x^6 + 3*x^4 - x^2 + x))

x^27 + 3*x^26 + 3*x^24 - x^22 + x^21 + x^12 + 4*x^11 + 3*x^10 + x^9 - 2*x^8 - x^7 - 15*x^6 + 4*x^5 - 7*x^4 - 3*x^3 + 4*x^2 - 3*x

In [83]:
(x^20 + x^5 + x^4 - 2*x^2 + x - 3) * (x^7 + 3*x^6 + 3*x^4 - x^2 + x)

x^27 + 3*x^26 + 3*x^24 - x^22 + x^21 + x^12 + 4*x^11 + 3*x^10 + x^9 - 2*x^8 - x^7 - 15*x^6 + 4*x^5 - 7*x^4 - 3*x^3 + 4*x^2 - 3*x

In [99]:
for fn in ["nasob_skolne", "karacuba"]:
    print(timeit(f"{fn}(R.random_element((-1, 200), x=-100, y=100), R.random_element((-1, 200), x=-100, y=100))", number=1000))

1000 loops, best of 3: 24 ms per loop
1000 loops, best of 3: 21.3 ms per loop
